In [7]:
import openrouteservice as ors
import folium
import matplotlib.cm as cm
import matplotlib.colors as cl

# define colors
def color(value, maxValue):
    colors = ['#e31c00', '#aa5500', '#718e00', '#39c600', '#00ff00']
    N = len(colors)
    binSize = maxValue / N
    
    for i in range(N):
        if value < binSize*(i+1):
            return colors[i]
        

# create map centered on Heidelberg
m = folium.Map(location = [49.411085, 8.685894], zoom_start = 13)

heidelberg = [[8.655705,49.395446],[8.718184,49.434366]]
heidelberg_folium = [list(reversed(coord)) for coord in heidelberg]

# request centrality from ors
host = "http://localhost:8082/ors"
profile = "driving-car"
client = ors.Client(base_url=host, key='5b3ce3597851110001cf6248554c879acee241f6bc733402d2d351be')
resp = client.request(url = f'/v2/centrality/{profile}/json', get_params = {},requests_kwargs = {"timeout":None}, post_json = {'bbox': heidelberg})

# visualize rectangle
folium.Rectangle(bounds=heidelberg_folium, color='#fcba03', fill=True, fill_color='#fcba03').add_to(m) 
maxValue = max(resp['centralityScores'])

# display centrality on map
count = 0
for loc in resp['locations']:
    loc[0], loc[1] = loc[1], loc[0]
    folium.CircleMarker(location = loc, tooltip = resp['nodeIds'][count], radius = 1, color=color(resp['centralityScores'][count], maxValue)).add_to(m)
    count += 1

m

In [4]:
ors_resp = resp

import json

with open('/tmp/api_test_logs/run_tests/centrality_test_failure_response.txt') as log_txt:
    gh_resp = json.load(log_txt)
    
m = folium.Map(location = [49.411085, 8.685894], zoom_start = 13)

# visualize rectangle
folium.Rectangle(bounds=heidelberg_folium, color='#fcba03', fill=True, fill_color='#fcba03').add_to(m) 
maxValue = max(resp['centralityScores'])

# display centrality on map
count = 0
for loc in gh_resp['locations']:
    loc[0], loc[1] = loc[1], loc[0]
    folium.CircleMarker(location = loc, tooltip=gh_resp['nodeIds'][count], radius = 1, color=color(gh_resp['centralityScores'][count], maxValue)).add_to(m)
    count += 1

m